# Week 3 Assignment Census Data
## Transportation profile Los Angeles
### Commuting times by neighborhoods 


### The following assignment looks to examine, visualize and represent the data collected from the percentages of workers that commute
### longer than 1 hour to their workplace around different neighborhoods in the LA County. This data is a first step to provide results from the places and amount of people that spend significant time getting to their workplace, understanding the complexity and future problems this situation brings to the wellbeing of citizens and their quality of life


### Jose Portales

In [137]:
# First, provide workstation. import pandas to provide library for data exploration
# provide entrance for downloaded data

In [138]:
import pandas as pd
import geopandas as gpd
neighborhoods=gpd.read_file('incneigh.geojson')

In [139]:
#shorten the data and generate a new dataframe with the deisred information.We only need specific variables and info

columns_to_keep = ['OBJECTID',
                   'spa',
                   'Neighborhood',
                   'sup_dist',
                  'geometry']

In [140]:
neighborhoods2 = neighborhoods[columns_to_keep]

In [141]:
#Create another variable trimming another information, this time 2 rows that contain information about the unwanted neighborhoods(islands below)

neighborhoods3 = neighborhoods2.drop([11, 207])

In [142]:
#Import csv file with the % of commute time above 1 hour by neighborhood in LA County
commute=pd.read_csv('CTLC3.csv', delimiter=';')


In [143]:
#For the upcoming merge, we want to change the name of the variable "neighborhood" to allow the merge to work
commute.rename(columns={'name': 'Neighborhood'}, inplace=True)


In [144]:
#merge based on common element

merged_df = neighborhoods3.merge(commute,on='Neighborhood')



In [145]:
City_boundary=gpd.read_file('City_Boundary.geojson')

In [146]:
import geopandas as gpd

# Assuming merged_df and City_boundary are already defined and loaded as GeoDataFrames

# Clip the merged_df by the City_boundary
clipped_gdf = gpd.clip(merged_df, City_boundary)


In [147]:
LA_Commute=clipped_gdf

In [148]:
#Load income data for the multilayer map
LA_Income=gpd.read_file('MedianIncome.geojson')

In [149]:
import folium

In [150]:
print(LA_Commute['Commute Time Above 1 Hour'].dtype)
# If the column is not of a numeric type, convert it
LA_Commute['Commute Time Above 1 Hour'] = pd.to_numeric(LA_Commute['Commute Time Above 1 Hour'], errors='coerce')


float64


In [151]:
# Fill missing values with a default value, for example, 0
LA_Commute['Commute Time Above 1 Hour'].fillna(0, inplace=True)


In [152]:
LA_Commute_geojson = LA_Commute.to_json()

In [153]:
import pandas as pd

# Assuming 'Commute Time Above 1 Hour' is the column you're interested in
quantile_list = [0, .2, .4, .6, .8, 1.]
quantiles = LA_Commute['Commute Time Above 1 Hour'].quantile(quantile_list)

# Convert quantiles to a list to use as bins
bins = quantiles.tolist()


In [154]:
pip install --upgrade jenkspy


Note: you may need to restart the kernel to use updated packages.


In [155]:
import jenkspy

# Assuming LA_Commute['Commute Time Above 1 Hour'] is a valid Series with numerical data
values = LA_Commute['Commute Time Above 1 Hour'].dropna().values  # Ensure no NaN values and convert to numpy array

# Attempt to calculate natural breaks directly
breaks = jenkspy.jenks_breaks(values, 5)  # Here, '5' is the number of desired classes

print(breaks)


[0.0, 7.78, 12.13, 15.36, 20.46, 32.67]


In [156]:
import folium

# Assuming LA_Commute_geojson contains your GeoJSON data
# and LA_Commute is a DataFrame with 'Neighborhood' and 'Commute Time Above 1 Hour' data

# Natural breaks determined previously
breaks = [0.0, 7.78, 12.13, 15.36, 20.46, 32.67]

# Initialize a map centered on a rough average location of your data
m = folium.Map(location=[33.9, -118.2], zoom_start=10,tiles='CartoDB positron', attribution='CartoDB')

# Add the Choropleth layer using the natural breaks for classification
# Adjust line_opacity for thinner borders
folium.Choropleth(
    geo_data=LA_Commute_geojson,
    name='choropleth',
    data=LA_Commute,
    columns=['Neighborhood', 'Commute Time Above 1 Hour'],
    key_on='feature.properties.Neighborhood',
    fill_color='YlOrRd',  # A color palette that reflects the data's distribution
    fill_opacity=0.7,
    line_opacity=0.1,  # Make borders thinner
    legend_name='Commute Time Above 1 Hour (%)',
    bins=breaks,  # Use the provided natural breaks here
).add_to(m)

# Add GeoJson layer for neighborhood names
folium.GeoJson(
    LA_Commute_geojson,
    name='Neighborhood Names',
    style_function=lambda x: {'color': 'transparent', 'fillColor': 'transparent', 'weight': 0},
    tooltip=folium.GeoJsonTooltip(
        fields=['Neighborhood'],
        aliases=['Neighborhood:'],
        style=("background-color: white; color: #333333; font-family: Arial; font-size: 12px; padding: 10px; border-radius: 2px; border: 1px solid black;"),
        sticky=True
    )
).add_to(m)

# Ensure layer control is added to toggle different layers on the map
folium.LayerControl().add_to(m)

# Display the map
m


In [157]:
df = pd.read_excel('Median Household Income - 2022.xlsx')
# examine the shape of the data (# of rows and columns)


In [158]:
df = df[['name','Median Household Income']]


In [159]:
neighborhoods=gpd.read_file('LA_Neighborhoods.geojson')


In [160]:
neighborhoods = neighborhoods[['name','geometry']]


In [161]:
neighborhoods_income=neighborhoods.merge(df,on="name")

In [162]:
neighborhoods_income.columns = ['Neighborhood',
'geometry',
'Median Household Income ($)']

In [163]:
# Convert to a projected CRS (e.g., UTM zone 11N for parts of California)
neighborhoods_income = neighborhoods_income.to_crs(epsg=32611)


In [164]:
neighborhoods_income['centroid'] = neighborhoods_income['geometry'].centroid


In [165]:
# Convert centroids back to WGS84 to get latitude and longitude
neighborhoods_income['centroid'] = neighborhoods_income['centroid'].to_crs(epsg=4326)

neighborhoods_income['Latitude'] = neighborhoods_income['centroid'].y
neighborhoods_income['Longitude'] = neighborhoods_income['centroid'].x


In [166]:
import folium
import numpy as np
from branca.element import Template, MacroElement

# Initialize a Folium map of the City of L.A.
m = folium.Map(location=[34.0549, -118.2426], zoom_start=10, tiles='CartoDB positron')

# Adjusted calculate_radius function for a more balanced representation
def calculate_radius(income, min_income, max_income):
    normalized_income = (income - min_income) / (max_income - min_income)
    return 20 + (normalized_income ** 1.5) * 3000  # Adjusted scaling for circle sizes

# Adjusted get_color function for a blue-green-yellow color gradient
def get_color(income, min_income, max_income):
    normalized_income = (income - min_income) / (max_income - min_income)
    if normalized_income < 0.2:
        return '#ffffcc'  # Yellow for lowest incomes
    elif normalized_income < 0.4:
        return '#c2e699'
    elif normalized_income < 0.6:
        return '#78c679'
    elif normalized_income < 0.8:
        return '#31a354'
    else:
        return '#006837'  # Dark green for highest incomes

# Calculate min and max income for normalization
min_income = neighborhoods_income['Median Household Income ($)'].min()
max_income = neighborhoods_income['Median Household Income ($)'].max()

# Iterate through the GeoDataFrame to add circles
for index, row in neighborhoods_income.iterrows():
    lat = row['centroid'].y
    lon = row['centroid'].x
    radius = calculate_radius(row['Median Household Income ($)'], min_income, max_income)
    color = get_color(row['Median Household Income ($)'], min_income, max_income)
    
    folium.Circle(
        location=(lat, lon),
        radius=radius,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.7,
        tooltip=f"{row['Neighborhood']}: ${row['Median Household Income ($)']}"
    ).add_to(m)

# Custom Legend with Numeric Ranges and Updated Title
template = """
{% macro html(this, kwargs) %}
<div style="position: fixed; 
            bottom: 50px; left: 50px; width: 250px; height: 160px; 
            background-color: white; border:2px solid grey; z-index:9999; font-size:14px;
            padding: 10px;">
&nbsp; <strong>Median Household Income ($)</strong> <br>
&nbsp; > $100,000 &nbsp; <i class="fa fa-circle fa-1x" style="color:#006837"></i><br>
&nbsp; $80,000 - $100,000 &nbsp; <i class="fa fa-circle fa-1x" style="color:#31a354"></i><br>
&nbsp; $60,000 - $80,000 &nbsp; <i class="fa fa-circle fa-1x"style="color:#78c679"></i><br>
&nbsp; $40,000 - $60,000 &nbsp; <i class="fa fa-circle fa-1x" style="color:#c2e699"></i><br>
&nbsp; < $40,000 &nbsp; <i class="fa fa-circle fa-1x" style="color:#ffffcc"></i>
</div>
{% endmacro %}
"""

macro = MacroElement()
macro._template = Template(template)

m.get_root().add_child(macro)

# Display the map
m


In [167]:
import folium
import numpy as np
from branca.element import Template, MacroElement

# Initialize a Folium map of the City of L.A.
m = folium.Map(location=[34.0549, -118.2426], zoom_start=10, tiles='CartoDB positron', attribution='CartoDB')

# Add the Choropleth layer for commute times
folium.Choropleth(
    geo_data=LA_Commute_geojson,
    name='Commute Time',
    data=LA_Commute,
    columns=['Neighborhood', 'Commute Time Above 1 Hour'],
    key_on='feature.properties.Neighborhood',
    fill_color='YlOrRd',
    fill_opacity=0.7,
    line_opacity=0.1,
    legend_name='Commute Time Above 1 Hour (%)',
    bins=breaks,
).add_to(m)

# Add circles for median household income
# Define a function to scale the median income to a suitable radius
def calculate_radius(income, min_income, max_income):
    normalized_income = (income - min_income) / (max_income - min_income)
    return 20 + (normalized_income ** 1.5) * 3000

# Define a function for the color gradient
def get_color(income, min_income, max_income):
    normalized_income = (income - min_income) / (max_income - min_income)
    if normalized_income < 0.2:
        return '#ffffcc'
    elif normalized_income < 0.4:
        return '#c2e699'
    elif normalized_income < 0.6:
        return '#78c679'
    elif normalized_income < 0.8:
        return '#31a354'
    else:
        return '#006837'

# Calculate min and max income for normalization
min_income = neighborhoods_income['Median Household Income ($)'].min()
max_income = neighborhoods_income['Median Household Income ($)'].max()

# Iterate through the GeoDataFrame to add circles
for index, row in neighborhoods_income.iterrows():
    lat = row['centroid'].y
    lon = row['centroid'].x
    radius = calculate_radius(row['Median Household Income ($)'], min_income, max_income)
    color = get_color(row['Median Household Income ($)'], min_income, max_income)
    
    folium.Circle(
        location=(lat, lon),
        radius=radius,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.7,
        tooltip=f"{row['Neighborhood']}: ${row['Median Household Income ($)']}"
    ).add_to(m)

# Add layer control to toggle between layers
folium.LayerControl().add_to(m)

# Display the map
m


In [168]:
import os

# Print the current working directory
print(os.getcwd())

# Optionally, change the directory
# os.chdir('/path/to/directory')

# Then save the map
m.save('LA_Neighborhoods_Map.html')

/home/jovyan/week5


In [169]:
import folium
import numpy as np
from branca.element import Template, MacroElement

# Initialize a Folium map of the City of L.A.
m = folium.Map(location=[34.0549, -118.2426], zoom_start=10, tiles='CartoDB positron', attribution='CartoDB')

# Assuming LA_Commute_geojson and neighborhoods_income are already defined

# Add the Choropleth layer for commute times
folium.Choropleth(
    geo_data=LA_Commute_geojson,
    name='Commute Time',
    data=LA_Commute,
    columns=['Neighborhood', 'Commute Time Above 1 Hour'],
    key_on='feature.properties.Neighborhood',
    fill_color='YlOrRd',
    fill_opacity=0.7,
    line_opacity=0.1,
    legend_name='Commute Time Above 1 Hour (%)',
    bins=[0.0, 7.78, 12.13, 15.36, 20.46, 32.67],
).add_to(m)

# Function to calculate circle radius
def calculate_radius(income, min_income, max_income):
    normalized_income = (income - min_income) / (max_income - min_income)
    return 20 + (normalized_income ** 1.5) * 3000

# Function to determine circle color
def get_color(income, min_income, max_income):
    normalized_income = (income - min_income) / (max_income - min_income)
    if normalized_income < 0.2:
        return '#ffffcc'
    elif normalized_income < 0.4:
        return '#c2e699'
    elif normalized_income < 0.6:
        return '#78c679'
    elif normalized_income < 0.8:
        return '#31a354'
    else:
        return '#006837'

# Calculate min and max income for normalization
min_income = neighborhoods_income['Median Household Income ($)'].min()
max_income = neighborhoods_income['Median Household Income ($)'].max()

# Add circles for median household income
for index, row in neighborhoods_income.iterrows():
    folium.Circle(
        location=[row['centroid'].y, row['centroid'].x],
        radius=calculate_radius(row['Median Household Income ($)'], min_income, max_income),
        color=get_color(row['Median Household Income ($)'], min_income, max_income),
        fill=True,
        fill_color=get_color(row['Median Household Income ($)'], min_income, max_income),
        fill_opacity=0.7,
        tooltip=f"{row['Neighborhood']}: ${row['Median Household Income ($)']}"
    ).add_to(m)

# Custom Legend for Median Household Income
legend_html = '''
<div style="position: fixed; 
            bottom: 50px; left: 50px; width: 250px; height: 150px; 
            background-color: white; border:2px solid grey; z-index:9999; font-size:14px;
            padding: 10px;">
    <strong>Median Household Income ($)</strong><br>
    > $100,000 &nbsp; <i style="background-color: #006837; width: 12px; height: 12px; display: inline-block; opacity: 0.7;"></i><br>
    $80,000 - $100,000 &nbsp; <i style="background-color: #31a354; width: 12px; height: 12px; display: inline-block; opacity: 0.7;"></i><br>
    $60,000 - $80,000 &nbsp; <i style="background-color: #78c679; width: 12px; height: 12px; display: inline-block; opacity: 0.7;"></i><br>
    $40,000 - $60,000 &nbsp; <i style="background-color: #c2e699; width: 12px; height: 12px; display: inline-block; opacity: 0.7;"></i><br>
    < $40,000 &nbsp; <i style="background-color: #ffffcc; width: 12px; height: 12px; display: inline-block; opacity: 0.7;"></i>
</div>
'''

legend = MacroElement()
legend._template = Template(legend_html)

m.get_root().add_child(legend)

# Add layer control to toggle between layers
folium.LayerControl().add_to(m)

# Display the map
m


In [170]:
# Save the map as html
m.save("interactive_income_map.html")